# To-Do

- ...

# Computational Structural Design II <br/> Intro to Milling

### Learning Goal: 
- orient block & panel to be milled on a machine bed
- try to fit more than one block into the panel
- determine cutting paths
- output machining datasets

## First, a brief overview...


### In this lesson we will use:
- TBD

### Step One is to Plan


<!-- ![Wirecutting Flowchart](img/milling_flowchart.png) -->
<img src="img/milling_flowchart.png" width="500">

### Content:
- [Determine Machine](#1)
- [Import Blocks](#a)
- [Generate Blanks](#b)
- [Orient on Machining Table](#c)
- [Prepare for Wire Path](#d)
- [Generate Wire Path](#e)


### Exercise:
- Exercise 4.5 Orient blocks in panel 
- Exercise 4.6 Place panels w/ blocks on Machine Bed
- Exercise 4.7 Generate CNC Paths & Output
</br>
---

### Determine a Machine

As there were many types of wire-cutting machines, there are also many milling machines. Milling machines can be quite common, and there are benefits and drawbacks to the different types of machines that can 

# Possible Types of Machines

| Wirecutting Type     | Image                                                     | Possible Materials                    |
| :--------------------: | :---------------------------------------------------------: | :-------------------------------------: |
| 5-axis Milling Machine      | <img src="img/cnc_milling_5axis.png" width="800"> | Any                                  |
| Robotic Arm Milling | <img src="img/robotic_arm_milling.png" width="800">  | Any |




While **Robotic Arm Milling** affords more flexibility in machine bed size and the geometries which can possibly be milled, there is a drawback to the accuracy of the mill. Alternatively, 5-axis milling is much more precise, however the machine bed size is dependent on the machine manufacturer and the possible geometries are limited.

According to [wmtcnc.com](https://www.wmtcnc.com/news/new-5-axis-machining-centre-from-germany/), a company which designs milling machines, the volume within which the block or panel must fit is **815 x 510 x 510 mm**. We will use this as our guide.

So we can already set our `machine_dim` variable for the rest of the workflow.

In [1]:
machine_dim = [815, 510, 510]

## Let's begin the workflow...

<a id='a'></a>
# Importing Blocks <br/>
## Preparation:
Locate the `.json` file with the exported discretized blocks.

## Step 1: Import the file and turn it into a usable format


In [2]:
#import the relavant libraries
import compas
from compas.datastructures import Mesh

#read the data
data = compas.json_load("placeholder.json")
# grab the Mesh from the data by reading it and automatically defining it as a Mesh
mesh: Mesh = data['mesh']

In [3]:
from compas_notebook.app import App

viewer = App()
viewer.add(mesh)
viewer.show()

/opt/miniconda3/envs/csd2/lib/python3.8/site-packages/IPython/core/display.py:724: UserWarning: Consider using IPython.display.IFrame instead
  warnings.warn("Consider using IPython.display.IFrame instead")


## Step 2: Re-orient the Blocks

This next step requires us to first give some local xyz orientation to the blocks themselves, and then align that orientation to the world xyz. we use the datatype of frames in order to do define these axes, then use different frames to compare them to each other and define translations. Think of it this way...

Frame Translations???



In [4]:
from compas.geometry import Frame, Rotation, Transformation

In [5]:
# First, reset the orientation which is defined in the json

mesh.update_default_face_attributes(left=False)
mesh.update_default_face_attributes(top=False)
mesh.update_default_face_attributes(front=False)

In [6]:
from compas.geometry import Vector
# Identify left, top, bottom, and front

# Sort the faces based on the size of the dot product
# of the unitized face normal and the negative X axis.
# The last element of the sorted list has the highest value
# and thus is the "most parallel" with this direction.


left = sorted(mesh.faces(), key=lambda face: Vector(* mesh.face_normal(face, unitized=True)).dot([1,0,0]))[-1]
mesh.face_attribute(left, 'left', True)


top = sorted(mesh.faces(), key=lambda face: Vector(* mesh.face_normal(face, unitized=True)).dot([0,0,1]))[-1]
mesh.face_attribute(top, 'top', True)
bottom = sorted(mesh.faces(), key=lambda face: Vector(* mesh.face_normal(face, unitized=True)).dot([1,0,0]))[0]
mesh.face_attribute(bottom, 'bottom', True)

front = sorted(mesh.faces(), key=lambda face: Vector(* mesh.face_normal(face, unitized=True)).dot([0,1,0]))[-1]
mesh.face_attribute(front, 'front', True)

In [7]:
from compas_notebook.app import App

viewer = App()
viewer.add(mesh)
viewer.show()

## Step 3: Alignment

Now we must sort out the alignment by aligning the face of the block which is determined to be the bottom with the worldXY. This requires building frames, and from these frames building transformations.

In [8]:
from compas.geometry import bestfit_frame_numpy
from compas.geometry import Frame, Rotation, Transformation
from compas.datastructures import Mesh
from compas.geometry import Frame
from compas.geometry import Plane

from compas.geometry import oriented_bounding_box_numpy
from compas.geometry import Box

from compas_view2.app import App

from compas.geometry import Scale, Translation, Rotation

In [9]:
left = list(mesh.faces_where({'left': True}))[0]
top = list(mesh.faces_where({'top': True}))[0]
front = list(mesh.faces_where({'front': True}))[0]
bottom = list(mesh.faces_where({'bottom': True}))[0]

In [10]:
# Compute a bestfit frame for the left face of the mesh
# using the bottom is what works in my code 
# Use the coordinates of the corners of the face as input for the bestfit function.

corners = mesh.face_coordinates(bottom)

In [11]:
# This frame has some rotation to it, so not a vertical frame. Has a tilt
frame = Frame(*bestfit_frame_numpy(corners))

new_frame = frame

In [12]:
# Since the face is 2D,
# the frame might be roto-reflected.
# If that is the case, rotate it by 180 degrees around the frame y axis.

if new_frame.zaxis.dot([1, 0, 0]) < 0:
    angle_rad = 3.14159
    R = Rotation.from_axis_and_angle(new_frame.yaxis, angle_rad, point=new_frame.point)
    new_frame.transform(R)

In [13]:
# Reorient the mesh by aligning the frame with the world coordinate system.
# To do that, compute a frame-to-frame transformation,
# and apply it to the mesh and the frame.

world = Frame.worldXY()

X = Transformation.from_frame_to_frame(new_frame, world)

new_mesh = mesh.transformed(X)

In [14]:
from compas_notebook.app import App

viewer = App()
viewer.add(new_mesh)
viewer.show()

## Step 4: Blank Material

Now we will generate the blank material from which the block is going to be cut. This step entails finding the `oriented bounding box` of our block which we are cutting.

In [15]:
from compas.geometry import Frame, Box
from compas.geometry import Scale
from compas.datastructures import Mesh
from compas.geometry import oriented_bounding_box_numpy

mesh = new_mesh

In [16]:
# Compute the bounding box of the mesh.
# And convert it into a box geometry object.

bbox = mesh.vertices_attributes('xyz', keys=mesh.vertices())
box = oriented_bounding_box_numpy(bbox)
blank = Box.from_bounding_box(box)
blank_unsized = Box.from_bounding_box(box)
bbf = blank.frame

In [17]:
# Add some padding to the blank,
# by scaling it by 10% in all directions.
# Use the frame of the blank as basis for the scaling.

blank.transform(Scale.from_factors([1.10, 1.10, 1.10], frame=bbf))
thickness_blank = (blank.zsize - blank_unsized.zsize)/2

In [18]:
from compas_notebook.app import App

viewer = App()
viewer.add(new_mesh)
viewer.add(blank)
viewer.show()

## Step 5: Machining Table

The next step is to generate a plane which will represent the table upon which our material will be cut.

In [19]:
from compas.geometry import Plane

table_plane = Plane([0,0,0],machine_dim)

print(machine_dim)

[815, 510, 510]


In [20]:
def make_boundary_points(dimensions):
    x = dimensions[0]
    y = dimensions[1]
    points = [[0,0,0],[x,0,0],[x,y,0],[0,y,0]]
    return points
        

In [21]:
table = Mesh.from_points(make_boundary_points(machine_dim))
print(table)

<Mesh with 4 vertices, 2 faces, 5 edges>


In [22]:
from compas_notebook.app import App

viewer = App()
viewer.add(table)
viewer.add(new_mesh)
viewer.show()

In [23]:
# This table is oriented differently from seen on the slides
# and the frame is off-center

# table = Mesh.from_meshgrid(dx=3, dy=4, nx=2, ny=2)
frame = Frame([1.5, 0, 0], [1, 0, 0], [0, 1, 0])

table.attributes['frame'] = frame

## Step 6: Placement on Table

The next step is to generate a plane which will represent the table upon which our material will be cut.

In [24]:
# Place the blank and the mesh on the cutting table by
# 1. computing a frame-to-frame transformation between the frame of the blank and the frame of the table.
# 2. defining a translation over half the blank size in the y direction and half the blank size in the z direction
# 3. applying the combined transformation to both mesh and blank

# This transformation still leaves the block hovering... makes no sense?
X = Transformation.from_frame_to_frame(blank.frame, table.attributes['frame'])

# Seems my xsize and ysize are associated with wrong axes?
T = Translation.from_vector([0, 0.5 * blank.xsize, thickness_blank])

S, H, R, Tr, P = X.decomposed()

In [25]:
new_mesh.transform(Tr * T)
blank.transform(Tr * T)

In [26]:
from compas_notebook.app import App

viewer = App()
# viewer.add(table)
viewer.add(blank)
viewer.add(new_mesh)
viewer.show()

## Step 7: Organize Edges for Wirepath

The next step is

In [27]:
from compas.geometry import Point, Line, Box
from compas.geometry import dot_vectors
from compas.datastructures import Mesh

from compas.geometry import Vector

In [28]:
# Find the left face of the mesh in the current orientation.

left = sorted(mesh.faces(), key=lambda face: Vector(* mesh.face_normal(face, unitized=True)).dot([1,0,0]))[-1]


In [29]:
# Identify the vertices of the left face.

left_vertices = mesh.face_vertices(left)

In [30]:
# Identify the bottom-front most vertex of the left face (left-bottom-front => lbf).

lbf = sorted(left_vertices, key=lambda vertex: mesh.vertex_coordinates(vertex, 'zy'))[0]

lbf_point = Point(* mesh.vertex_coordinates(lbf))

In [31]:
# Find the index of the lbf in the list of vertices of the left face.

lbf_index = left_vertices.index(lbf)

In [32]:
# Reorder the vertices of the left face such that they start at the lbf.

left_cycle = left_vertices[lbf_index:] + left_vertices[:lbf_index]

In [33]:
# Identify the matching right cycle
# by finding for each vertex of the left cycle
# a neighbouring vertex that does not belong to the left cycle.

right_cycle = []
for vertex in left_cycle:
#     print(vertex)
    for nbr in mesh.vertex_neighbors(vertex):
#         print(nbr)
        if nbr not in left_cycle:
            right_cycle.append(nbr)
            break

In [34]:
for u, v in zip(left_cycle, right_cycle):
    a = mesh.vertex_coordinates(u)
    b = mesh.vertex_coordinates(v)
#     viewer.add(Line(a,b), linewidth=10, color=(1, 0, 0))

## Step 8: Wires

Doot doot

In [35]:
from compas.geometry import Point, Line, Polyline, Plane, Box
from compas.geometry import dot_vectors
from compas.geometry import intersection_line_plane
from compas.datastructures import Mesh

In [36]:
# Planes

left_plane = Plane([0, 0, 0], [-1, 0, 0])
right_plane = Plane([3, 0, 0], [+1, 0, 0])

In [37]:
# Wire

wires = [(left_plane.point, right_plane.point)]

In [38]:
# Compute the full wires
# by intersecting the line segments defined by matching left and right vertices
# with the left and right plane.

for u, v in zip(left_cycle, right_cycle):
    a = mesh.vertex_coordinates(u)
    b = mesh.vertex_coordinates(v)
    line = Line(a, b)

    a = Point(* intersection_line_plane(line, left_plane))
    b = Point(* intersection_line_plane(line, right_plane))

    wires.append((a, b))

wires.append(wires[1])
wires.append(wires[0])

## Bonus Step: Animation

In [39]:
# # Viz

# viewer = App(width=1600, height=900)
# viewer.view.camera.rz = +50
# viewer.view.camera.rx = -70
# viewer.view.camera.ty = -0.7
# viewer.view.camera.distance = 1.8

# viewer.add(mesh)
# viewer.add(blank, opacity=0.5)
# viewer.add(table, show_edges=True, facecolor=(0.9, 0.9, 0.9), linecolor=(1.0, 1.0, 1.0))

# for a, b in wires:
#     viewer.add(Line(a, b), linewidth=10, color=(1, 0, 0))